In [1]:
import pandas as pd
import numpy as np 
import geopandas as gpd 
from geopy.geocoders import Nominatim
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC 
import folium
from folium import Choropleth, Circle, Marker
from folium.plugins import HeatMap, MarkerCluster
from branca.colormap import LinearColormap



In [2]:
higher = pd.read_excel("5.2. Численность студентов организаций высшего образования.xls")
aftermid = pd.read_excel("Численность студентов ТИПО.xls")
#select year 2022 data from both files 
high = higher.iloc[7:, [-1]]
colleges = aftermid.iloc[5:, [-2]]

high.reset_index(drop=True, inplace=True)
colleges.reset_index(drop=True, inplace=True)

high.rename(columns = {'Unnamed: 23': 'unis_2022'}, inplace = True)
colleges.rename(columns = {'Unnamed: 23': 'colleges_2022'}, inplace = True)

students1 = pd.concat([high, colleges], axis = 1)

In [9]:
regions = higher.iloc[7:28, [0]]
regions.reset_index(drop = True, inplace= True)

students1['regions'] = regions
students1.drop([21], inplace = True)

In [13]:
#rename the regions 

In [16]:
from translate import Translator
translator= Translator(from_lang = 'ru', to_lang="en")

def perevod(df):
    for region in df['regions']:
        translation = translator.translate(region)
        for rgname in gdf.ADM1_EN.unique(): 
            if translation.capitalize()[:3] == rgname[:3]:
                df.loc[df['regions'] ==region, 'regions'] = rgname
                break
    return df 

In [17]:
students1 = perevod(students1)

In [18]:
#merge the geographical shapefile with region names 

In [19]:
students1.loc[students1['regions'] == 'Жетису', 'regions'] = 'Jetisu Region'
students1.loc[students1['regions'] == 'Жамбылская', 'regions'] = 'Jambyl Region'


In [20]:
student_total = students1

In [21]:
student_total['unis_colleges'] = student_total['unis_2022'] +student_total['colleges_2022']
student_total.drop(columns = ['unis_2022', 'colleges_2022'], axis = 1, inplace = True)
student_total.drop(0, inplace = True)
student_total.set_index('regions', inplace = True)

gdf = gdf[['ADM1_EN', 'geometry']].set_index('ADM1_EN')
gdf.index.name = 'regions'

In [28]:
student_total.iloc[3, 0] = 'Almaty Region' #fixing the effect of the earlier translator function 

In [29]:
student_total.set_index('regions', inplace = True)

In [4]:
student_total = pd.read_csv('unis_colleges.csv')
gdf = gpd.read_file("kaz_adm_unhcr_2023_SHP/kaz_admbnda_adm1_unhcr_2023.shp")

In [37]:
map1 = folium.Map(location=[48.0196, 66.9237], tiles="cartodbpositron", zoom_start=6)

folium.Choropleth(
    geo_data=gdf.to_crs("EPSG:4326").__geo_interface__, # here we use `.to_crs`
    name="choropleth",
    data=student_total,
    columns=["regions", "unis_colleges"], # folium requires 2 columns
    key_on="feature.properties.ADM1_EN",  # replace ADM1_EN if needed
    fill_color="YlGnBu",
    legend_name="Number of students per region 2023",
).add_to(map1)
map1


In [ ]:
"""
I created an interactive map using showing number of students in each region and number of colleges and universities.
There were several difficulties in this project:
1. Scraping the data about the names of the unis and colleges. Each was scraped from reliable websites (egov.kz and _____)
2. The other difficulty was Geocoding, meaning transforming the regular pandas Data Frame into a Geo data frame. 
3. Combining several kinds of maps on a single one 
All in all I combined data from 4 different sources to complete this project.
Libraries that I have used: 
Tutorials: 
GitHub: with the sourcecode 
"""

In [12]:

website = 'https://egov.kz/cms/ru/articles/2Ftechnical_spisok'
path = r'C:Program Files (x86)\chromedriver.exe'
service = Service(executable_path = 'chromedriver.exe')

driver = webdriver.Chrome()
driver.get(website)


elements = driver.find_elements(By.XPATH, "//h3[@class = 'slidedown-title toggle']")
WebDriverWait(driver, 30).until(
    EC.presence_of_element_located((By.XPATH, "//h3[@class = 'slidedown-title toggle']")))
for element in elements:
    element.click()  

college_names = []
college_addresses = []
college_type = []
td_index = 1
rows = driver.find_elements(By.XPATH,'//tr')
parentRows = driver.find_elements(By.XPATH, "//tr[.//tr]")
city_region = driver.find_elements(By.XPATH, "//h3[@class = 'slidedown-title toggle opened']")
reg_inx = 0
#astana almaty VKO have text inside TD, others td->p, some tds have several ps(the name of an institution is divided into two ps)
#after executing it, I found out that the structure for Kostanay region and Astana differs from the rest(there are nested tr's, which makes the code 
#execute these tables twice: once the whole, then only by index
dividers = ['Контингент всего', 'Колледжи государственной формы собственности', 'Атырауская область', '№ п/п', 'Наименование колледжа', 'электронный адрес', 'эл. адрес', 'электронная почта']

for row in rows:
    if row in parentRows: 
        continue 
    elif row.find_element(By.XPATH, './td[1]').text.strip().strip('.') in [str(x) for x in range(100)]:
        text = row.find_element(By.XPATH, './td[2]').text
        # college_names.append(text)
        try: 
            if text in colleges.loc[colleges.city_region == 'Астана', 'names'].unique() or text in colleges.loc[colleges.city_region == 'Акмолинская область', 'names'].unique():
                # td_inx = 5
                college_addresses.append(row.find_element(By.XPATH, './td[5]').text)
            elif text in colleges.loc[colleges.city_region == 'Шымкент', 'names'].unique():
                # td_inx = 6
                college_addresses.append(row.find_element(By.XPATH, './td[6]').text)
            else:
                # td_inx = 3
                college_addresses.append(row.find_element(By.XPATH, './td[3]').text)
            
            # college_addresses.append(row.find_element(By.XPATH, f'./td[{td_inx}]').text)

        except:
            continue

    else:
        # college_names.append(row.find_element(By.XPATH, './td[1]').text)
        try:
            college_addresses.append(row.find_element(By.XPATH, './td[2]').text)
        except:
            continue  

driver.quit()
    

In [3]:
colleges = pd.read_csv('final_notdel.csv')
college_addresses= pd.read_csv('college_addresses.csv')

In [14]:
# college_addresses = pd.DataFrame(college_addresses, columns = ['address'])
# colleges = pd.DataFrame(college_names, columns = ['names'])

In [16]:
# college_addresses.to_csv('college_addresses.csv')

In [6]:
to_delete = ['Не государственные  колледжи', 'Государственные колледжи (КГУ)', 'Колледжи районов', 'Государственные колледжи (КГКП)', 
             'Колледжи при ВУЗах', '№', 'Государственные колледжи',       'Частные колледжи',
             'Государственные колледжи (КГУ)', 'Негосударственные колледжи', 'Колледжи при ВУЗах', 'Колледжи при КУИС МЮ РК',
             'г.Алматы Колледжи негосударственной формы собственности','Атырауская область',
             '№\nп/п', 'Колледжи районов', 'Государственные колледжи (КГКП)', 'Наименование учебного заведения', 'Адрес']


In [7]:
# for city in colleges.city_region:
#     governmental  = True 
#     for college in colleges.loc[colleges.city_region == city, 'names']:
#         if college in  ['Частные колледжи',  'Не государственные  колледжи', 'Негосударственные колледжи', 'г.Алматы Колледжи негосударственной формы собственности']:
#            governmental  = False
#         elif college in  ['Государственные колледжи (КГУ)','Колледжи районов', 'Государственные колледжи (КГКП)', 'Колледжи при ВУЗах', 'Колледжи при КУИС МЮ РК']:
#            governmental  = True
#         colleges.loc[colleges.names == college, 'public1'] = governmental

In [8]:
# colleges.to_csv('final_notdel.csv')

In [9]:
colleges.drop(colleges[colleges.names.isin(to_delete)].index, inplace = True)

In [10]:
college_addresses.drop(college_addresses[college_addresses.address.isin(to_delete)].index, inplace = True)

In [11]:
# here im finding div points and creating a new column for general  region name as some addresses may be repeated
# points = []
# points.append(colleges.loc[colleges.names == 'Колледж информационных технологий при ТОО «Astana IT University»'].index)
# points.append(colleges.loc[colleges.names == 'ТОО «Гуманитарно-экономический колледж города Алматы»'].index)
# points.append(colleges.loc[colleges.names == 'Колледж новых технологий имени Манапа Утебаева'].index)
# points.append(colleges.loc[colleges.names == 'Учреждение «Колледж Максат»'].index)
# points.append(colleges.loc[colleges.names == 'ЧУ «Колледж медресе Актобе»'].index)
# points.append(colleges.loc[colleges.names == 'Медицинский колледж «Дауа»'].index)
# points.append(colleges.loc[colleges.names == 'Колледж «Мед-Профи» (частный)'].index)
# points.append(colleges.loc[colleges.names == 'НОУ «Западно-Казахстанский инженерно- экономический колледж»'].index)
# points.append(colleges.loc[colleges.names == 'Һибатулла Тарази медресе-колледжі'].index)
# points.append(colleges.loc[colleges.names == 'Технико-экономический колледж при  Карагандинском государственном индустриальном университете'].index)
# points.append(colleges.loc[colleges.names == 'Учреждение «Костанайский высший экономический колледж Казпотребсоюза»'].index)
# points.append(colleges.loc[colleges.names == 'Болашақ медицина колледжі'].index)
# points.append(colleges.loc[colleges.names == 'Мангистауский высший многопрофильный колледж «Келешек»'].index)
# points.append(colleges.loc[colleges.names == 'Учреждение «Екибастузский гуманитарно- технический колледж»'].index)
# points.append(colleges.loc[colleges.names == 'ТОО «Колледж инновационного профессионального развития»'].index)  #
# points.append(colleges.loc[colleges.names == 'КГУ «УстьКаменогорский колледж № 1»'].index)
# points.append(colleges.loc[colleges.names == 'Государственное коммунальное предприятие на праве хозяйственного ведения «Жетысайский высший медицинский колледж» управления общественного злоровья Туркестанской области»'].index)

# colleges.loc[0:37, 'city_region'] = 'Астана'
# colleges.loc[38:123, 'city_region'] = 'Алматы'
# colleges.loc[124:134, 'city_region'] = 'Шымкент'
# colleges.loc[135:168, 'city_region'] = 'Акмолинская область'
# colleges.loc[169:212, 'city_region'] = 'Актюбинская область'
# colleges.loc[213:287, 'city_region'] = 'Алматинская область'
# colleges.loc[288:313, 'city_region'] = 'Атырауская область'
# colleges.loc[314:348, 'city_region'] = 'Западно-Казахстанкая область'
# colleges.loc[349:392, 'city_region'] = 'Жамбылская область'
# colleges.loc[393:465, 'city_region'] = 'Карагандинская область'
# colleges.loc[466:500, 'city_region'] = 'Костанайская область'
# colleges.loc[501:534, 'city_region'] = 'Кызылординская область'
# colleges.loc[535:562, 'city_region'] = 'Мангистауская область'
# colleges.loc[563:613, 'city_region'] = 'Павлодарская область'
# colleges.loc[614:639, 'city_region'] = 'Северо-Казахстанская область'
# colleges.loc[640:689, 'city_region'] = 'Восточно-Казахстанская область'
# colleges.loc[690:718, 'city_region'] = 'Туркестанская область'




In [14]:
colleges.reset_index(inplace = True)

In [15]:
college_addresses.reset_index(inplace = True)

In [16]:
len(colleges) == len(college_addresses)

True

In [21]:
colleges

index  Unnamed: 0.1  Unnamed: 0  \
0        2             2           2   
1        3             3           3   
2        4             4           4   
3        5             5           5   
4        6             6           6   
..     ...           ...         ...   
683    714           714         714   
684    715           715         715   
685    716           716         716   
686    717           717         717   
687    718           718         718   

                                                 names            city_region  \
0    ГККП «Строительно-технический колледж» акимата...                 Астана   
1    ГККП «Колледж общественного питания и сервиса»...                 Астана   
2    ГККП «Технологический колледж» акимата города ...                 Астана   
3     ГККП «Технический колледж» акимата города Астана                 Астана   
4    КГУ «Профессионально-технический колледж» аким...                 Астана   
..                                                 ...                    ...   
683  Государственное  коммунальное казенное предпри...  Туркестанская область   
684  Государственное  коммунальное казенное предпри...  Туркестанская область   
685  Государственное коммунальное казенное предприя...  Туркестанская область   
686  Государственное коммунальное предприятие на пр...  Туркестанская область   
687  Государственное коммунальное предприятие на пр...  Туркестанская область   

     public1                            address  
0       True       ул. Аль-Фараби, 53/350-16-06  
1       True           ул. Б.Майлин, 1250-16-47  
2       True       ул. С.Сейфуллина, 5954-42-14  
3       True                Улица 187,здание 19  
4       True  Кургальджинское шоссе, 2257-05-46  
..       ...                                ...  
683     True                          Туркестан  
684     True                            Шымкент  
685     True                       Сарыагашский  
686     True                          Туркестан  
687     True                        Жетысайский  

[688 rows x 7 columns]

In [19]:
colleges['address']  = college_addresses.address

In [28]:
colleges['full_address'] = colleges.city_region + ' ' + colleges.address

In [29]:
colleges.to_csv("final.csv")

In [5]:
#for unis 

website = 'https://egov.kz/cms/ru/articles/2Fvusi_rk'
path = r'C:Program Files (x86)\chromedriver.exe'
service = Service(executable_path = 'chromedriver.exe')

driver = webdriver.Chrome()
driver.get(website)


els = driver.find_elements(By.XPATH, "//h3[@class = 'slidedown-title toggle']")
WebDriverWait(driver, 30).until(
    EC.presence_of_element_located((By.XPATH, "//h3[@class = 'slidedown-title toggle']")))
for element in els:
    element.click()  

uni_name = []
uni_address = []
td_index = 1
rows = driver.find_elements(By.XPATH,'//tr')
parentRows = driver.find_elements(By.XPATH, "//tr[.//tr]")

for row in rows:
    if row in parentRows: 
        continue 
    elif row.find_element(By.XPATH, './td[1]').text.strip().strip('.') in [str(x) for x in range(100)]:
        uni_name.append(row.find_element(By.XPATH, './td[2]').text)
        try:
            uni_address.append(row.find_element(By.XPATH, './td[3]').text)
        except:
            continue
    # else:
    #     uni_name.append(row.find_element(By.XPATH, './td[1]').text)
    #     uni_address.append(row.find_element(By.XPATH, './td[3]').text)



driver.quit()


    

In [23]:
# unis = pd.DataFrame({'names': uni_name, 'address': uni_address})

In [6]:
colleges = pd.read_csv('colleges_wgeo.csv', index_col = None)
unis = pd.read_csv('fixed_f.csv', index_col = None)

In [7]:
#saving so i dont have to scrape all the time 
# unis.to_csv('unis_edited.csv')
def add_comma_after_word(text, word):
    return text.replace(word, f"{word},")

# Apply the function to the 'text' column
colleges['full_address'] = colleges['full_address'].apply(lambda x: add_comma_after_word(x, 'область'))

# colleges['full_address']

In [18]:
from geopy.geocoders import ArcGIS
geolocator_arcgis = ArcGIS()
#geocoding colleges
for college in colleges['full_address'].iloc[467:]: #because of the interruptions, geocoding was done in batches, concurrently checking isna rows in colleges dataframe
    try:
        location = geolocator_arcgis.geocode(college)
        colleges.loc[colleges.full_address == college, 'Latitude'] = location.point.latitude
        colleges.loc[colleges.full_address == college, 'Longitude'] = location.point.longitude 

    except:
        #paste the region coordinates 
        region = colleges.loc[colleges.full_address == college, 'city_region']
        location = geolocator_arcgis.geocode(region)
        colleges.loc[colleges.full_address == college, 'Latitude'] = location.point.latitude
        colleges.loc[colleges.full_address == college, 'Longitude'] = location.point.longitude 

In [27]:
from geopy.geocoders import ArcGIS
geolocator_arcgis = ArcGIS()
for uni in unis['address'].iloc[6:]:
    try:
        location = geolocator_arcgis.geocode(uni)
        unis.loc[unis.address == uni, 'Lat'] = location.point.latitude
        unis.loc[unis.address == uni, 'Long'] = location.point.longitude 
        unis.loc[unis.address == uni, 'Geocoded_address'] = location.address 

    except:
        div_point = uni.index(',')
        city_reg = uni[:div_point].strip('г.')
        location = geolocator_arcgis.geocode(city_reg)
        unis.loc[unis.address == uni, 'Lat'] = location.point.latitude
        unis.loc[unis.address == uni, 'Long'] = location.point.longitude
        unis.loc[unis.address == uni, 'Geocoded_address'] = location.address 



In [39]:
# there are for unis that are out of kz in the map
#1.        'Левый Берег, Архангельск, Архангельская область',
#2        '北海道札幌市, 0060002', 
#'060014, București', 'Жангирхан',
#3        '060011, București',
outside = ['Левый Берег, Архангельск, Архангельская область','北海道札幌市, 0060002', '060014, București','060011, București']
#find these unis and manually enter their geolocation
unis.loc[unis.Geocoded_address.isin(outside)]
unis.loc[unis.Geocoded_address == '060011, București', ['Lat', 'Long']] = [47.098177172135394, 51.91158816757311]
unis.loc[unis.Geocoded_address == '北海道札幌市, 0060002', ['Lat', 'Long']] = [47.131676271999844, 51.94092385007191]
unis.loc[unis.Geocoded_address == '060014, București', ['Lat', 'Long']] = [47.11142561224475, 51.893237523395804]
unis.loc[unis.Geocoded_address == 'Левый Берег, Архангельск, Архангельская область', ['Lat', 'Long']] = [44.82979512641042, 65.51269792696189]


In [24]:
unis.loc[3, ['Lat', 'Long']] = [51.18734046442033, 71.40905963647391]
unis.loc[0, ['Lat', 'Long']] = [51.15995604435302, 71.46716618554095]
unis.loc[10, ['Lat', 'Long']] = [51.14484991821989, 71.42261175432898]


In [25]:
unis.to_csv('fixed_f.csv')

In [30]:
# # Add points to the map
# import math 

# mc = MarkerCluster()
# for idx, row in colleges.iterrows():
#     if not math.isnan(row['Longitude']) and not math.isnan(row['Latitude']):
#         mc.add_child(Marker([row['Latitude'], row['Longitude']]))
# # m.add_child(mc)
# # m

In [31]:
# mc_unis = MarkerCluster()
# for idx, row in unis.iterrows():
#     if not math.isnan(row['Long']) and not math.isnan(row['Lat']):
#         mc_unis.add_child(Marker(location = [row['Lat'], row['Long']], popup=row['Geocoded_address'], icon=folium.Icon(color='green')))
# # m.add_child(mc_unis)

# # folium.LayerControl().add_to(m)

# # m

In [11]:
colleges

Unnamed: 0.3  Unnamed: 0.2  index  Unnamed: 0.1  Unnamed: 0  \
0               0             0      2             2           2   
1               1             1      3             3           3   
2               2             2      4             4           4   
3               3             3      5             5           5   
4               4             4      6             6           6   
..            ...           ...    ...           ...         ...   
683           683           683    714           714         714   
684           684           684    715           715         715   
685           685           685    716           716         716   
686           686           686    717           717         717   
687           687           687    718           718         718   

                                                 names            city_region  \
0    ГККП «Строительно-технический колледж» акимата...                 Астана   
1    ГККП «Колледж общественного питания и сервиса»...                 Астана   
2    ГККП «Технологический колледж» акимата города ...                 Астана   
3     ГККП «Технический колледж» акимата города Астана                 Астана   
4    КГУ «Профессионально-технический колледж» аким...                 Астана   
..                                                 ...                    ...   
683  Государственное  коммунальное казенное предпри...  Туркестанская область   
684  Государственное  коммунальное казенное предпри...  Туркестанская область   
685  Государственное коммунальное казенное предприя...  Туркестанская область   
686  Государственное коммунальное предприятие на пр...  Туркестанская область   
687  Государственное коммунальное предприятие на пр...  Туркестанская область   

     public1                            address  \
0       True       ул. Аль-Фараби, 53/350-16-06   
1       True           ул. Б.Майлин, 1250-16-47   
2       True       ул. С.Сейфуллина, 5954-42-14   
3       True                Улица 187,здание 19   
4       True  Кургальджинское шоссе, 2257-05-46   
..       ...                                ...   
683     True                          Туркестан   
684     True                            Шымкент   
685     True                       Сарыагашский   
686     True                          Туркестан   
687     True                        Жетысайский   

                                 full_address   Latitude  Longitude  
0         Астана ул. Аль-Фараби, 53/350-16-06  51.158934  71.525588  
1             Астана ул. Б.Майлин, 1250-16-47  51.177600  71.433000  
2         Астана ул. С.Сейфуллина, 5954-42-14  51.169827  71.388128  
3                  Астана Улица 187,здание 19  51.174629  71.389438  
4    Астана Кургальджинское шоссе, 2257-05-46  51.148670  71.386617  
..                                        ...        ...        ...  
683          Туркестанская область, Туркестан  43.298816  68.265085  
684            Туркестанская область, Шымкент  43.502413  68.486085  
685       Туркестанская область, Сарыагашский  41.497600  69.344100  
686          Туркестанская область, Туркестан  43.298816  68.265085  
687        Туркестанская область, Жетысайский  40.896794  68.255856  

[688 rows x 12 columns]

In [12]:
unis

Unnamed: 0.3  Unnamed: 0.2  Unnamed: 0.1  Unnamed: 0  \
0               0             0             0           0   
1               1             1             1           1   
2               2             2             2           2   
3               3             3             3           3   
4               4             4             4           4   
..            ...           ...           ...         ...   
101           101           101           101         101   
102           102           102           102         102   
103           103           103           103         103   
104           104           104           104         104   
105           105           105           105         105   

                                                 names  \
0    Евразийский национальный университет им.Л.Н.Гу...   
1          Казахский национальный университет искусств   
2          Казахская национальная академия хореографии   
3    Казахский агротехнический университет им. С.Се...   
4                       Медицинский университет Астана   
..                                                 ...   
101                      Alikhan Bokeikhan University    
102                      Медицинский университет Семей   
103            Университет имени Шакарима города Семей   
104            Жетысуский университет им.И.Жансугурова   
105      Жезказганский университет им. О.А.Байконурова   

                                     address        Lat       Long  \
0                  г. Астана, ул. Сатпаева 2  51.159956  71.467166   
1                  Астана, Тәуелсіздік, 50,   51.122810  71.472880   
2        г. Астана, проспект Улы дала, дом 9  51.098217  71.419256   
3                    г.Астана, пр. Женис, 62  51.187340  71.409060   
4            г. Астана, ул. Бейбітшілік 49 а  51.181491  71.416358   
..                                       ...        ...        ...   
101  г. Семей, ул. Абая Кунанбаева, дом 94/1  50.406105  80.244662   
102                  г. Семей, ул. Абая, 103  50.406004  80.248286   
103                г. Семей, ул. Глинки, 20А  50.399048  80.212657   
104     г.Талдыкорган, ул.Жансугурова, 187 А  45.008658  78.349892   
105          г. Жезказган, пр. Алашахана, 1Б  47.803467  67.715302   

                                      Geocoded_address  
0                                               Астана  
1              Тәуелсіздік даңғылы 50, Астана, Z00T2A5  
2                 Улы Дала проспект 9, Астана, Z05K7Y2  
3                                               Астана  
4              Бейбітшілік көшесі 49А, Астана, Z10K9D9  
..                                                 ...  
101  Абая Кунанбаева улица 94, Семей, Абайская обла...  
102  Абая площадь 103, Семей, Абайская область, F16...  
103          Глинки улица 20А, Семей, Абайская область  
104  Жансугурова улица 187А, Талдыкорган, Жетысуска...  
105  Алашахана даңғылы 1Б, Жезқазған, Жезқазған қал...  

[106 rows x 9 columns]

In [14]:
unis['uni'] = True 
colleges['uni'] = False

In [17]:
#since clusters overlap create a single dataframe 
kz_unis_colleges = pd.DataFrame()

In [15]:
kz_unis_colleges = pd.concat([unis, colleges], ignore_index = True)

In [18]:
kz_unis_colleges['names'] = pd.concat([unis.names, colleges.names], ignore_index = True)

In [20]:
kz_unis_colleges['Lat'] = pd.concat([unis.Lat, colleges.Latitude], ignore_index = True)

In [22]:
kz_unis_colleges['Long'] = pd.concat([unis.Long, colleges.Longitude], ignore_index = True)


In [25]:
kz_unis_colleges['uni'] = pd.concat([unis.uni, colleges.uni], ignore_index = True)


In [40]:
kz_unis_colleges.to_csv('kz_unis_colleges.csv')

In [39]:
mc_unis_colleges = MarkerCluster()

for idx, row in kz_unis_colleges.iterrows():
    if not math.isnan(row['Long']) and not math.isnan(row['Lat']):
        mc_unis_colleges.add_child(Marker(location=[row['Lat'], row['Long']],icon=folium.Icon(color='red' if row['uni'] == False else 'green')))

map1.add_child(mc_unis_colleges)                             

map1

In [41]:
map1.save('kz_unis_colleges_2022.html')